# Notebook for testing Caption Generator Program Code

### Importing Necessary Modules

In [ ]:
import string
import numpy as np
from PIL import Image
from pickle import dump, load
import numpy as np
from tensorflow.keras.applications.xception import Xception, preprocess_input
from tensorflow.keras.preprocessing.image import load_img, img_to_array
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.layers import add
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.layers import Input, Dense, LSTM, Embedding, Dropout
from tqdm.notebook import tqdm
tqdm().pandas()

2024-11-26 17:38:25.690159: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-11-26 17:38:25.700165: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1732660705.712101  620970 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1732660705.715458  620970 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-11-26 17:38:25.726626: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

0it [00:00, ?it/s]

# Step 1: Download dataset from Kaggle

In [1]:
import os
from import_dataset import ImportData

current_dir = os.getcwd()
destination_path = os.path.join(current_dir, 'dataset')

DataImport = ImportData()

DataImport.download(destination_path)

Path to dataset files: /home/npate145/.cache/kagglehub/datasets/nunenuh/flickr8k/versions/2
Files and folders copied successfully.


### Set Path for the Input Caption Text File and Image Dataset

In [2]:
current_dir = os.getcwd()
dataset_path = os.path.join(current_dir, 'dataset')
# print(dataset_path)

caption_text = dataset_path + '/' + 'captions.txt'
image_files = dataset_path + '/' + 'images'
print(caption_text, image_files)

/home/npate145/Documents/MS_in_AI/ece5831-2024/Project/ece5831-2024-final-project/dataset/captions.txt /home/npate145/Documents/MS_in_AI/ece5831-2024/Project/ece5831-2024-final-project/dataset/images


# Step 2: Input Data Processing: Test InputDataProcessing() Class
### Create a vocabulary of unique caption texts after cleaning and save cleaned texts in a file

In [3]:
# Import DataProcessing module
from data_processing import InputDataProcessing

DataProcess = InputDataProcessing()

texts = DataProcess.load_data(caption_text)

description = DataProcess.image_description(texts)
print(f'Caption Description Raw: \n{description}')

cleaned_text = DataProcess.clean_data(description)
print(f'Caption Description After Cleaning: \n{cleaned_text}')

vocabulary = DataProcess.text_vocabulary(cleaned_text)
print(f'Unique Vocabulary List: \n{vocabulary}')

DataProcess.save_descriptions(cleaned_text, 'vocabulary.txt')

Caption Description Raw: 
{'1000268201_693b08cb0e.jpg': ['A little girl in a pink dress going into a wooden cabin .'], '1001773457_577c3a7d70.jpg': ['Two dogs on pavement moving toward each other .'], '1002674143_1b742ab4b8.jpg': ['Young girl with pigtails painting outside in the grass .'], '1003163366_44323f5815.jpg': ['man laying on bench holding leash of dog sitting on ground'], '1007129816_e794419615.jpg': ['The man with pierced ears is wearing glasses and an orange hat .'], '1007320043_627395c3d8.jpg': ['The small child climbs on a red ropes on a playground .'], '1009434119_febe49276a.jpg': ['A dog runs on the green grass near a wooden fence .'], '1012212859_01547e3f17.jpg': ['White dog with brown ears standing near water with head turned to one side .'], '1015118661_980735411b.jpg': ['Smiling boy in white shirt and blue jeans in front of rock wall with man in overalls behind him .'], '1015584366_dfcec3c85a.jpg': ['The black dog jumped the tree stump .'], '101654506_8eb26cfb60.jpg

In [23]:
# all_train_captions = []
# for key, val in descriptions.items():
#     for cap in val:
#         all_train_captions.append(cap)

# # Consider only words which occur at least 8 times in the corpus
# word_count_threshold = 8
# word_counts = {}
# nsents = 0
# for sent in all_train_captions:
#     nsents += 1
#     for w in sent.split(' '):
#         word_counts[w] = word_counts.get(w, 0) + 1

# vocab = [w for w in word_counts if word_counts[w] >= word_count_threshold]

# print('preprocessed words %d ' % len(vocab))


# Step 3: Extract Features

In [ ]:
from extract_features import ExtractFeatures

FeatureExtract = ExtractFeatures()

features = FeatureExtract.extract_features(image_files, 'Xception')

FeatureExtract.save_feature_model(features, 'features.pkl')

I0000 00:00:1732654288.596818  419351 gpu_device.cc:2022] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 4268 MB memory:  -> device: 0, name: NVIDIA RTX A3000 Laptop GPU, pci bus id: 0000:01:00.0, compute capability: 8.6


  0%|          | 0/8091 [00:00<?, ?it/s]

I0000 00:00:1732654290.288695  419806 service.cc:148] XLA service 0x7f1c80003a90 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
I0000 00:00:1732654290.288714  419806 service.cc:156]   StreamExecutor device (0): NVIDIA RTX A3000 Laptop GPU, Compute Capability 8.6
2024-11-26 15:51:30.309216: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:268] disabling MLIR crash reproducer, set env var `MLIR_CRASH_REPRODUCER_DIRECTORY` to enable.
I0000 00:00:1732654290.491479  419806 cuda_dnn.cc:529] Loaded cuDNN version 90300


1/1 ━━━━━━━━━━━━━━━━━━━━ 3s 3s/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step


I0000 00:00:1732654292.576720  419806 device_compiler.h:188] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━

In [5]:
from extract_features import ExtractFeatures

FeatureExtract = ExtractFeatures()
features = FeatureExtract.load_feature_model(open("features.pkl","rb"))

# Step 4: Create Train, Validation and Test Dataset Files

In [6]:
from dataset_builder import DatasetBuilder

DataSetBuild = DatasetBuilder()

DataSetBuild.file_name_extractor(image_files)
DataSetBuild.split_dataset()
DataSetBuild.save_files(dataset_path)

['3030823649_3b7b6c728d.jpg', '238512430_30dc12b683.jpg', '2586911841_41b7a48c91.jpg', '2465497494_43d74df57c.jpg', '371522748_dc557bcd6c.jpg', '390992388_d74daee638.jpg', '3711030008_3872d0b03f.jpg', '501320769_31eea7b7ea.jpg', '3737492755_bcfb800ed1.jpg', '3726629271_7639634703.jpg', '2289212650_69de7a20b2.jpg', '1392272228_cf104086e6.jpg', '2940594396_20c40947b0.jpg', '3162095736_cc41dd41ff.jpg', '451326127_2d95a2e1c2.jpg', '3262301835_9f1a49b80a.jpg', '2637904605_fc355816fc.jpg', '3331102049_bc65cf6198.jpg', '3417662443_2eaea88977.jpg', '1248940539_46d33ed487.jpg', '2915183095_4ed4aa4f37.jpg', '145721496_687af9bb18.jpg', '3532587748_7e64bb223a.jpg', '621000329_84f48948eb.jpg', '465994762_1760e83c5d.jpg', '3315033940_e91f87b7f2.jpg', '2338627102_6708a9b4fd.jpg', '3293596075_973b0bfd08.jpg', '805682444_90ed9e1ef3.jpg', '3585598356_8ce815bbb9.jpg', '3656906086_7034f69ab6.jpg', '2344699642_4fae2f4e07.jpg', '3266261886_36e1323d2f.jpg', '1417637704_572b4d6557.jpg', '2815745115_c8479d560c

# Step 5: Load Train Dataset

In [7]:
from load_train_dataset import LoadTrainDataset

TrainDataset = LoadTrainDataset()

train_file = dataset_path + '/' + 'train_dataset.txt'

#train = loading_data(filename)
train_imgs = TrainDataset.load_images(train_file)
train_descriptions = TrainDataset.load_clean_descriptions("vocabulary.txt")
print(f'train dataset description: \n{train_descriptions}')
train_features = TrainDataset.load_features(train_imgs)
print(f'train dataset features: \n{train_features}')

train dataset description: 
{'1000268201_693b08cb0e.jpg': ['<start> little girl in pink dress going into wooden cabin <end>'], '1001773457_577c3a7d70.jpg': ['<start> two dogs on pavement moving toward each other <end>'], '1009434119_febe49276a.jpg': ['<start> dog runs on the green grass near wooden fence <end>'], '1015118661_980735411b.jpg': ['<start> smiling boy in white shirt and blue jeans in front of rock wall with man in overalls behind him <end>'], '1015584366_dfcec3c85a.jpg': ['<start> the black dog jumped the tree stump <end>'], '101669240_b2d3e7f17b.jpg': ['<start> man on skis looking at artwork for sale in the snow <end>'], '1016887272_03199f49c4.jpg': ['<start> several climbers in row are climbing the rock while the man in red watches and holds the line <end>'], '1019604187_d087bf9a5f.jpg': ['<start> white dog running after yellow ball <end>'], '1022454332_6af2c1449a.jpg': ['<start> two people are at the edge of lake facing the water and the city skyline <end>'], '1022454428

In [44]:
#converting dictionary to clean list of descriptions
def dict_to_list(descriptions):
    all_desc = []
    for key in descriptions.keys():
        [all_desc.append(d) for d in descriptions[key]]
    return all_desc

#creating tokenizer class 
#this will vectorise text corpus
#each integer will represent token in dictionary 

def create_tokenizer(descriptions):
    desc_list = dict_to_list(descriptions)
    tokenizer = Tokenizer()
    tokenizer.fit_on_texts(desc_list)
    return tokenizer


In [45]:
# give each word a index, and store that into tokenizer.p pickle file
tokenizer = create_tokenizer(train_descriptions)
dump(tokenizer, open('tokenizer.p', 'wb'))
vocab_size = len(tokenizer.word_index) + 1
vocab_size 

7577

In [46]:
#calculate maximum length of descriptions
def max_length(descriptions):
    desc_list = dict_to_list(descriptions)
    return max(len(d.split()) for d in desc_list)

max_length = max_length(descriptions)
max_length

32

In [47]:
features['1000268201_693b08cb0e.jpg'][0]

array([0.47339642, 0.01732645, 0.07333968, ..., 0.08559059, 0.02102295,
       0.23766546], dtype=float32)

In [48]:
# Define the model

#1 Photo feature extractor - we extracted features from pretrained model Xception. 
#2 Sequence processor - word embedding layer that handles text, followed by LSTM 
#3 Decoder - Both 1 and 2 model produce fixed length vector. They are merged together and processed by dense layer to make final prediction

In [50]:
#create input-output sequence pairs from the image description.

#data generator, used by model.fit_generator()
def data_generator(descriptions, features, tokenizer, max_length):
    while 1:
        for key, description_list in descriptions.items():
            #retrieve photo features
            feature = features[key][0]
            input_image, input_sequence, output_word = create_sequences(tokenizer, max_length, description_list, feature)
            yield [[input_image, input_sequence], output_word]         

def create_sequences(tokenizer, max_length, desc_list, feature):
    X1, X2, y = list(), list(), list()
    # walk through each description for the image
    for desc in desc_list:
        # encode the sequence
        seq = tokenizer.texts_to_sequences([desc])[0]
        # split one sequence into multiple X,y pairs
        for i in range(1, len(seq)):
            # split into input and output pair
            in_seq, out_seq = seq[:i], seq[i]
            # pad input sequence
            in_seq = pad_sequences([in_seq], maxlen=max_length)[0]
            # encode output sequence
            out_seq = to_categorical([out_seq], num_classes=vocab_size)[0]
            # store
            X1.append(feature)
            X2.append(in_seq)
            y.append(out_seq)
    return np.array(X1), np.array(X2), np.array(y)

In [53]:
[a,b],c = next(data_generator(train_descriptions, features, tokenizer, max_length))
a.shape, b.shape, c.shape

((47, 2048), (47, 32), (47, 7577))

In [54]:
from keras.utils import plot_model

# define the captioning model
def define_model(vocab_size, max_length):
    
    # features from the CNN model squeezed from 2048 to 256 nodes
    inputs1 = Input(shape=(2048,))
    fe1 = Dropout(0.5)(inputs1)
    fe2 = Dense(256, activation='relu')(fe1)

    # LSTM sequence model
    inputs2 = Input(shape=(max_length,))
    se1 = Embedding(vocab_size, 256, mask_zero=True)(inputs2)
    se2 = Dropout(0.5)(se1)
    se3 = LSTM(256)(se2)

    # Merging both models
    decoder1 = add([fe2, se3])
    decoder2 = Dense(256, activation='relu')(decoder1)
    outputs = Dense(vocab_size, activation='softmax')(decoder2)
    
    # tie it together [image, seq] [word]
    model = Model(inputs=[inputs1, inputs2], outputs=outputs)
    model.compile(loss='categorical_crossentropy', optimizer='adam')
    
    # summarize model
    print(model.summary())
    plot_model(model, to_file='model.png', show_shapes=True)
    
    return model

In [55]:
# train our model
print('Dataset: ', len(train_imgs))
print('Descriptions: train=', len(train_descriptions))
print('Photos: train=', len(train_features))
print('Vocabulary Size:', vocab_size)
print('Description Length: ', max_length)

model = define_model(vocab_size, max_length)
epochs = 10
steps = len(train_descriptions)
# making a directory models to save our models
os.mkdir("models")
for i in range(epochs):
    generator = data_generator(train_descriptions, train_features, tokenizer, max_length)
    model.fit_generator(generator, epochs=1, steps_per_epoch= steps, verbose=1)
    model.save("models/model_" + str(i) + ".h5")

Dataset:  6000
Descriptions: train= 6000
Photos: train= 6000
Vocabulary Size: 7577
Description Length:  32


Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_6       │ (None, 32)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_5       │ (None, 2048)      │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding           │ (None, 32, 256)   │  1,939,712 │ input_layer_6[0]… │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout (Dropout)   │ (None, 2048)      │          0 │ input_layer_5[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_1 (Dropout) │ (None, 32, 256)   │          0 │ embedding[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ not_equal           │ (None, 32)        │          0 │ input_layer_6[0]… │
│ (NotEqual)          │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense (Dense)       │ (None, 256)       │    524,544 │ dropout[0][0]     │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm (LSTM)         │ (None, 256)       │    525,312 │ dropout_1[0][0],  │
│                     │                   │            │ not_equal[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ add_60 (Add)        │ (None, 256)       │          0 │ dense[0][0],      │
│                     │                   │            │ lstm[0][0]        │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_1 (Dense)     │ (None, 256)       │     65,792 │ add_60[0][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_2 (Dense)     │ (None, 7577)      │  1,947,289 │ dense_1[0][0]     │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 5,002,649 (19.08 MB)

 Trainable params: 5,002,649 (19.08 MB)

 Non-trainable params: 0 (0.00 B)

None
You must install pydot (`pip install pydot`) for `plot_model` to work.


AttributeError: 'Functional' object has no attribute 'fit_generator'